# FTX reader

In [1]:
import matplotlib
from datetime import *
%matplotlib inline
import cufflinks as cf
cf.go_offline()
cf.set_config_file(offline=False, world_readable=True)
import plotly.express as px
import nest_asyncio
nest_asyncio.apply()
import os,sys
sys.path.append('../')
from utils.io_utils import *
from histfeed.ftx_history import main

end_time=datetime.now(timezone.utc)-timedelta(days=1)#.replace(minute=0,second=0,microsecond=0)
start_time=end_time-timedelta(days=60)
halflife=timedelta(days=2)
modes=[('h','high'),('c','close'),('l','low'),('v','size')]

In [2]:
weights = pd.read_excel(os.path.join(os.sep, 'home','david',"config", "pfoptimizer",'current_weights.xlsx')).sort_values(by='optimalWeight',key=lambda f: np.abs(f),ascending=False)
coins = list(weights.set_index(['name']).drop(['USD','total']).head(5).index.map(lambda f: f.replace('-PERP','')))
weights

name        spot        mark       index    borrow  quote_borrow  \
11         USD         NaN         NaN         NaN       NaN           NaN   
10  MATIC-PERP    0.592356    0.591877    0.592596  0.134094      0.026772   
12       total         NaN         NaN         NaN       NaN           NaN   
9     BCH-PERP  118.250000  118.150000  118.280000  0.067047      0.026772   
8   1INCH-PERP    0.708600         NaN         NaN  0.040158      0.026772   
7     UNI-PERP    5.470000    5.462000    5.465090  0.011742      0.026772   
6     DOT-PERP    7.911000    7.901000    7.906787  0.120591      0.026772   
0    ATOM-PERP    8.297500    8.279500    8.293760  0.268071      0.026772   
5     MKR-PERP  978.500000  977.500000  977.786445  0.011742      0.026772   
4     BNB-PERP  231.003000  230.930000  230.962861  0.080433      0.026772   
3    LINK-PERP    7.068000    7.068000    7.071278  0.011742      0.026772   
1    USDT-PERP    0.999100    0.998800    0.999200  0.040158      0.026772   
2     XRP-PERP    0.371000    0.370850    0.370908  0.017613      0.026772   

    ExpectedBenchmark  funding  previousWeight  optimalWeight  ExpectedCarry  \
11           0.026772      NaN     1949.430937    3025.607272       0.000000   
10          -0.000598      NaN      237.995213    -851.818857     137.012275   
12          -0.032999      NaN      755.028029     755.028029     233.878411   
9           -0.000663      NaN        0.000000    -472.896159      43.812927   
8           -0.000352      NaN     -251.478400    -258.940809      16.735784   
7           -0.000264      NaN        0.000000    -230.229283      10.890447   
6           -0.000442      NaN     -779.661600    -197.667502       9.308002   
0           -0.000008      NaN      -77.945670     148.128147       4.950498   
5           -0.000150      NaN        0.000000    -137.833076       5.226365   
4           -0.000286      NaN     -302.090750     -78.384190       1.883447   
3           -0.000097      NaN      237.972000     -75.573834       1.783231   
1           -0.000163      NaN        0.000000     -59.753443       1.133315   
2           -0.000350      NaN        0.000000     -55.610236       1.142118   

    RealizedCarry     excessIM     excessMM  transactionCost  spotBenchmark  \
11            0.0  2987.855871  2708.876107                0       0.026772   
10            NaN -1144.944758 -1057.758592                0            NaN   
12            0.0    39.718762     0.000933                0       0.026772   
9             NaN  -571.208782  -526.905878                0            NaN   
8             NaN  -329.430252  -304.111595                0            NaN   
7             NaN  -278.092740  -256.523891                0            NaN   
6             NaN  -251.476989  -232.149500                0            NaN   
0             NaN   125.908925   128.871488                0            NaN   
5             NaN  -175.354302  -161.877291                0            NaN   
4             NaN   -94.679851   -87.336490                0            NaN   
3             NaN   -91.285237   -84.205162                0            NaN   
1             NaN   -70.401813   -64.916753                0            NaN   
2             NaN   -67.171312   -61.961510                0            NaN   

    FundingBenchmark                time  
11          0.000073 2022-06-24 08:00:00  
10               NaN 2022-06-24 08:00:00  
12          0.000073 2022-06-24 08:00:00  
9                NaN 2022-06-24 08:00:00  
8                NaN 2022-06-24 08:00:00  
7                NaN 2022-06-24 08:00:00  
6                NaN 2022-06-24 08:00:00  
0                NaN 2022-06-24 08:00:00  
5                NaN 2022-06-24 08:00:00  
4                NaN 2022-06-24 08:00:00  
3                NaN 2022-06-24 08:00:00  
1                NaN 2022-06-24 08:00:00  
2                NaN 2022-06-24 08:00:00

In [2]:
futures_df = main([None,'get','ftx','max'])

INFO:histfeed.ftx_history:Logger set
INFO:histfeed.ftx_history:Cannot find the nb_of_days param. Defaulting to nb_of_days=100
INFO:histfeed.ftx_history:histfeed running with params ['get', 'ftx', 'max']
INFO:histfeed.ftx_history:Getting history...


### rates markets

In [7]:
selected = [df for df in futures_df.columns if any(df.split('-')[0].split('_')[0]==coin for coin in (coins+['USD']))]
prices=futures_df[[c for c in selected if any(string in c for string in ['price_c'])]]

short_rates=futures_df[[c for c in selected if any(string in c for string in ['PERP_rate_c','rate_borrow'])]]
short_rates=short_rates.ewm(halflife=halflife,times=short_rates.index).mean()

borrow_size=futures_df[[c for c in selected if any(string in c for string in ['_rate_size','price_volume'])]]

for c in coins:
    long_perp_carry=short_rates[c+'-PERP_rate_c']-short_rates['USD_rate_borrow']
    short_perp_carry=-short_rates[c+'-PERP_rate_c']-short_rates[c+'_rate_borrow']
    short_rates[c+'_best_perp_carry']= pd.concat([long_perp_carry, short_perp_carry]).max(level=0)
   # long_rates[c+'_long_future_carry']=long_rates[c+'-1231_rate_c']-short_rates['USD_rate_borrow']
   # long_rates[c+'_short_future_carry']=-long_rates[c+'-1231_rate_c']-short_rates[c+'_rate_borrow']

short_rates
pd.concat([short_rates],axis=0).iplot()#))

/tmp/ipykernel_17589/1800538636.py:12: FutureWarning:

Using the level keyword in DataFrame and Series aggregations is deprecated and will be removed in a future version. Use groupby instead. df.median(level=1) should use df.groupby(level=1).median().

/tmp/ipykernel_17589/1800538636.py:12: FutureWarning:

Using the level keyword in DataFrame and Series aggregations is deprecated and will be removed in a future version. Use groupby instead. df.median(level=1) should use df.groupby(level=1).median().

/tmp/ipykernel_17589/1800538636.py:12: FutureWarning:

Using the level keyword in DataFrame and Series aggregations is deprecated and will be removed in a future version. Use groupby instead. df.median(level=1) should use df.groupby(level=1).median().

/tmp/ipykernel_17589/1800538636.py:12: FutureWarning:

Using the level keyword in DataFrame and Series aggregations is deprecated and will be removed in a future version. Use groupby instead. df.median(level=1) should use df.groupby(level=1)

In [8]:
pd.concat([short_rates.filter(like='borrow')],axis=0).iplot()#))

In [9]:
pd.concat([borrow_size],axis=0).iplot()#))

### carry directionality

In [10]:
plotthat = futures_df[['BNB-PERP/rate/h',
       'BNB-PERP/rate/l', 'BNB-PERP/rate/c']]
plotthat.columns=['h','l','c']

KeyError: "None of [Index(['BNB-PERP/rate/h', 'BNB-PERP/rate/l', 'BNB-PERP/rate/c'], dtype='object')] are in the [columns]"

In [11]:
import plotly.graph_objects as go
import numpy as np
fig = go.Figure()

fig.add_trace(go.Scatter(
    x=plotthat.index,#+x_rev,
    y=0.5*(plotthat['l'].values+plotthat['h'].values),
    fill='toself',
    fillcolor='rgba(0,100,80,0.2)',
    line_color='rgba(255,255,255,0)',
    showlegend=False,
    name='BNB',
))
fig.add_trace(go.Scatter(
    x=plotthat.index, y=plotthat['c'].values,
    line_color='rgb(0,100,80)',
    name='Fair',['1h','15s']
))

fig.update_traces(mode='lines')
fig.show()

NameError: name 'plotthat' is not defined

In [ ]:
pd.concat([prices,short_rates.filter(like='carry')],axis=0).iplot(secondary_y=list(prices.columns))

# stopout: show min/max of premiums

In [5]:
safe_gather_limit = 5

end_time=datetime.now(timezone.utc)#.replace(minute=0,second=0,microsecond=0)
start_time=end_time-timedelta(hours=1)
main([None,'build','ftx','wide','1','15s'])
granular_df = main([None,'get','ftx','wide','1','15s'])

INFO:histfeed.ftx_history:Logger set
INFO:histfeed.ftx_history:Cannot find the timeframe param. Defaulting to timeframe=1h
INFO:histfeed.ftx_history:histfeed running with params ['build', 'ftx', 'wide', '1', '15s']
INFO:histfeed.ftx_history:Building history for build timeframe=1h
INFO:histfeed.ftx_history:BUILDING COROUTINES
INFO:histfeed.ftx_history:0 coroutines gathered, nothing to do
INFO:histfeed.ftx_history:Logger set
INFO:histfeed.ftx_history:Cannot find the timeframe param. Defaulting to timeframe=1h
INFO:histfeed.ftx_history:histfeed running with params ['get', 'ftx', 'wide', '1', '15s']
INFO:histfeed.ftx_history:Getting history...


In [7]:
granular_df

1INCH-PERP_rate_funding  AAVE-PERP_rate_funding  \
2022-06-23 10:00:00                -0.157788                0.140256   
2022-06-23 11:00:00                -0.017532                0.192852   
2022-06-23 12:00:00                -0.201618                0.157788   
2022-06-23 13:00:00                -0.149022                0.043830   
2022-06-23 14:00:00                -0.070128                0.157788   
2022-06-23 15:00:00                 0.026298                0.149022   
2022-06-23 16:00:00                -0.043830               -0.219150   
2022-06-23 17:00:00                 0.026298               -0.236682   
2022-06-23 18:00:00                 0.061362               -0.175320   
2022-06-23 19:00:00                -0.017532               -0.236682   
2022-06-23 20:00:00                -0.166554               -0.149022   
2022-06-23 21:00:00                -0.192852               -0.078894   
2022-06-23 22:00:00                -0.035064               -0.070128   
2022-06-23 23:00:00                -0.087660               -0.026298   
2022-06-24 00:00:00                -0.184086                0.122724   
2022-06-24 01:00:00                -0.166554                0.105192   
2022-06-24 02:00:00                -0.131490                0.000000   
2022-06-24 03:00:00                -0.552258               -0.008766   
2022-06-24 04:00:00                -0.201618               -0.105192   
2022-06-24 05:00:00                -0.210384               -0.219150   
2022-06-24 06:00:00                -0.166554               -0.070128   
2022-06-24 07:00:00                 0.000000               -0.026298   
2022-06-24 08:00:00                -0.131490               -0.122724   
2022-06-24 09:00:00                -0.078894                0.017532   
2022-06-24 10:00:00                -0.113958               -0.236682   

                     ATOM-PERP_rate_funding  AVAX-PERP_rate_funding  \
2022-06-23 10:00:00               -0.043830               -0.061362   
2022-06-23 11:00:00                0.096426               -0.113958   
2022-06-23 12:00:00                0.026298               -0.070128   
2022-06-23 13:00:00                0.043830               -0.131490   
2022-06-23 14:00:00                0.026298               -0.096426   
2022-06-23 15:00:00                0.043830               -0.087660   
2022-06-23 16:00:00                0.061362               -0.262980   
2022-06-23 17:00:00                0.000000               -0.315576   
2022-06-23 18:00:00                0.000000               -0.280512   
2022-06-23 19:00:00               -0.061362               -0.368172   
2022-06-23 20:00:00               -0.078894               -0.166554   
2022-06-23 21:00:00               -0.008766                0.026298   
2022-06-23 22:00:00                0.043830                0.070128   
2022-06-23 23:00:00                0.043830                0.017532   
2022-06-24 00:00:00               -0.026298               -0.008766   
2022-06-24 01:00:00                0.245448                0.052596   
2022-06-24 02:00:00                0.061362                0.026298   
2022-06-24 03:00:00                0.017532                0.008766   
2022-06-24 04:00:00               -0.070128                0.043830   
2022-06-24 05:00:00               -0.043830                0.070128   
2022-06-24 06:00:00               -0.166554               -0.096426   
2022-06-24 07:00:00               -0.008766                0.017532   
2022-06-24 08:00:00               -0.166554                0.008766   
2022-06-24 09:00:00               -0.412002               -0.149022   
2022-06-24 10:00:00               -0.254214               -0.122724   

                     AXS-PERP_rate_funding  BCH-PERP_rate_funding  \
2022-06-23 10:00:00              -0.315576              -0.166554   
2022-06-23 11:00:00              -0.289278              -0.096426   
2022-06-23 12:00:00              -0.254214              -0.070128   
2022-06-23 13:00:00      

In [4]:
def compute_premium(df: pd.DataFrame,mode=1) -> pd.Series:
    return (df.filter(like='/mark/'+ modes[mode][0]).iloc[:,0]/df.filter(like='/indexes/'+modes[mode][1]).iloc[:,0]-1)*10000
def compute_premium_vs_spot(df: pd.DataFrame,mode=1) -> pd.Series:
    return (df.filter(like='/mark/'+ modes[mode][0]).iloc[:,0]/df.filter(like='/price/'+modes[mode][0]).iloc[:,0]-1)*10000
def compile_list(premium_list: list) -> pd.DataFrame:
    premium=premium_list[0]
    for df in premium_list[1:]:
        premium=premium.join(df,how='outer')
    return premium[~premium.index.duplicated()]

In [5]:
granular_df['premium']=compute_premium_vs_spot(granular_df)
prices=granular_df[[c+'/price/c' for c in coins]]
granular_df[['premium']].iplot()

AttributeError: 'NoneType' object has no attribute 'filter'

In [6]:
premium=compute_premium(granular_df,mode=0)
ewMax=premium.resample('1h').max()
ewMax=ewMax[~ewMax.index.duplicated()]
pd.concat([prices,ewMax],axis=0).iplot(secondary_y=list(prices.columns))

AttributeError: 'NoneType' object has no attribute 'filter'

In [7]:
premium=compute_premium(granular_df,mode=2)
ewMin=premium.resample('1h').min()
ewMin=ewMin[~ewMin.index.duplicated()]
pd.concat([prices,ewMin],axis=0).iplot(secondary_y=list(prices.columns))

AttributeError: 'NoneType' object has no attribute 'filter'